# Raw Event Log Data To Organized

In [0]:
from datetime import datetime, timedelta
import json
import gzip
import pyspark.sql.functions as F
import pyspark.sql.types as T
from pyspark.sql.types import (
    ArrayType,
    StructType,
    IntegerType,
    StringType,
    StructField,
    MapType,
)
from functools import reduce
import re

## Run this cell to drop the tables and start over

In [0]:
# To drop all tables and start over from eventlog files
if False:
    spark.sql("drop table physical_plan_keys;")
    spark.sql("drop table queries;")
    spark.sql("drop table operations;")
    print("Dropped the tables")

### 1. Inputs
- start_time: Timestamp default: yesterday()
- end_time: Timestamp default: time_now()

In [0]:
dbutils.widgets.text(
    "start_time", "yyyy-mm-dd HH:MM:SS", "StartTime, Format: yyyy-mm-dd HH:MM:SS"
)
dbutils.widgets.text(
    "end_time", "yyyy-mm-dd HH:MM:SS", "EndTime, Format: yyyy-mm-dd HH:MM:SS"
)

# get variables
start_time = dbutils.widgets.get("start_time")
end_time = dbutils.widgets.get("end_time")

# Because of work flows
time_now = datetime.now()

# Handle start_time conversion
if start_time == "None":
    # 2 weeks prior
    start_time = time_now - timedelta(days=14)
else:
    try:
        start_time = datetime.strptime(start_time, '%Y-%m-%d %H:%M:%S')
    except ValueError:
        raise ValueError('inputted start_time is not on the right format')

# Handle end_time conversion
if end_time == "None":
    end_time = time_now
else:
    try:
        end_time = datetime.strptime(end_time, '%Y-%m-%d %H:%M:%S')
    except ValueError:
        raise ValueError('inputted end_time is not on the right format')


assert start_time < end_time, "Start time needs to be before end time."

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-3025559219626018>:14
     11 end_time = dbutils.widgets.get("end_time")
     13 # Because of work flows
---> 14 time_now = datetime.now()
     16 # Handle start_time conversion
     17 if start_time == "None":
     18     # 2 weeks prior

NameError: name 'datetime' is not defined

### 2. Load Data From Table To DataFrame

In [0]:
query = f"SELECT * FROM eventlog_raw WHERE lastModified BETWEEN '{str(start_time)}' AND '{str(end_time)}'"
raw_df = spark.sql(query)

### 3. Extract Relevant Information From Data  
- Could be done by creating a function, then applying it to every row, but that might be slow.  
- Apply function to the column instead? Map function?  
- Check out built in functions first because of better performance.
- We got some work to do here to find the optimal solution.  

**Note**
- Events from file in table seem to be divided by '\n', so can be used to split (there is also a \n at the end which results in '' which needs to be removed dont know if this is true for all files but needs to be checked)  

**Keywords:**  
Regex, Lambda function, Built in functions

##### 3.1 Restructure fileData to fit JSON Format 
  1. Remove all newlines
  2. Find all }{ which represents new event starting and add a comma to divide
  3. Add brackets to whole string
  4. Use from_json to get on json format and add Schema

In [0]:
# Define Schema for fileData (Events)
schema = ArrayType(
    StructType(
        [
            StructField("Event", StringType(), True),
            StructField("SparkContext Id", StringType(), True),
            StructField("Stage Info", StringType(), True),
            StructField("Task Info", StringType(), True),
            StructField("Stage ID", StringType(), True),
            StructField("Task End Reason", StringType(), True),
            StructField("Stage IDs", StringType(), True),
            StructField("Stage Attempt ID", StringType(), True),
            StructField("Completion Time", StringType(), True),
            StructField("time", StringType(), True),
            StructField("errorMessage", StringType(), True),
            StructField("Task Executor Metrics", StringType(), True),
            StructField("Timestamp", StringType(), True),
            StructField("executionId", StringType(), True),
            StructField("Job Result", StringType(), True),
            StructField("Stage Infos", StringType(), True),
            StructField("details", StringType(), True),
            StructField("Task Metrics", StringType(), True),
            StructField("physicalPlanDescription", StringType(), True),
            StructField("modifiedConfigs", StringType(), True),
            StructField("Submission Time", StringType(), True),
            StructField("rootExecutionId", StringType(), True),
            StructField("Spark Version", StringType(), True),
            StructField("Rollover Number", StringType(), True),
            StructField("sparkPlanInfo", StringType(), True),
            StructField("Job ID", StringType(), True),
            StructField("Task Type", StringType(), True),
            StructField("description", StringType(), True),
            StructField("Properties", StringType(), True),
            StructField("accumUpdates", StringType(), True),
        ]
    )
)

# Modify format to be a JSON-list of events
df = raw_df.withColumn("fileData", F.regexp_replace("fileData", "\n", ""))
df = df.withColumn("fileData", F.regexp_replace("fileData", "\}\{", "},{"))
df = df.withColumn("fileData", F.concat(F.lit("["), df.fileData, F.lit("]")))
df = df.withColumn("fileData", F.from_json("fileData", schema))

##### 3.2 Explode And Expand JSON Data To Multiple Columns

In [0]:
# Define column list
columns = [
    "filePath",
    "clusterID",
    "clusterInstanceID",
    "sparkContextID",
    "lastModified",
    "eventlogKey",
]
# Explode json data list to independent rows
df2 = df.select(*columns, F.explode(df.fileData).alias("eventData"))
# Expand eventData column to multiple columns
df3 = df2.select(*columns, F.col("eventData.*"))

##### 3.3 Filter Out Relevant Events Into Dataframes

In [0]:
# Filter on all events for SQLExecutionStart and select keys related to this
sql_start_df = df3.select(
    df3.Event.alias("event_start"),
    "sparkContextID",
    "clusterInstanceID",
    "executionId",
    "rootExecutionId",
    "Description",
    "Details",
    "physicalPlanDescription",
    "sparkPlanInfo",
    df3.time.alias("time_start"),
    "modifiedConfigs",
    "eventlogKey",
).filter(
    df3.Event == "org.apache.spark.sql.execution.ui.SparkListenerSQLExecutionStart"
)

sql_end_df = df3.select(
    df3.Event.alias("event_end"),
    "sparkContextID",
    "clusterInstanceID",
    "executionId",
    df3.time.alias("time_end"),
    "errorMessage",
).filter(df3.Event == "org.apache.spark.sql.execution.ui.SparkListenerSQLExecutionEnd")

##### 3.4 Gather SQL Information

In [0]:
# Join star and end events for sql queries
sql_df = sql_start_df.join(
    sql_end_df,
    (sql_start_df.executionId == sql_end_df.executionId)
    & (sql_start_df.clusterInstanceID == sql_end_df.clusterInstanceID)
    & (sql_start_df.sparkContextID == sql_end_df.sparkContextID),
).drop(sql_end_df.executionId, sql_end_df.clusterInstanceID, sql_end_df.sparkContextID)
# above: drop sql_end columns to prevent duplicates in the resulting df

sql_df = sql_df.withColumn(
    "executionId", sql_df.executionId.cast("int")
)  # Cast id column to integer

sql_df = sql_df.withColumn(
    "time_start", sql_df.time_start.cast("double")
)  # Cast float
sql_df = sql_df.withColumn(
    "time_end", sql_df.time_end.cast("double")
)  # Cast float

sql_df = sql_df.sort(F.desc("executionId"))  # Sort by id ascending
# Calculate Duration of SQL Query
sql_df = sql_df.withColumn(
    "duration_ms", sql_df.time_end.cast("double") - sql_df.time_start.cast("double")
)

In [0]:
sql_df.show(10)

+--------------------+---------------+--------------------+--------------------+-----------------------+--------------------+-----------------+--------------------+-----------+--------------------+-------------------+--------------------+-----------+-----------------+------------+-----------+
|         event_start|rootExecutionId|         Description|             Details|physicalPlanDescription|       sparkPlanInfo|       time_start|     modifiedConfigs|eventlogKey|           event_end|     sparkContextID|   clusterInstanceID|executionId|         time_end|errorMessage|duration_ms|
+--------------------+---------------+--------------------+--------------------+-----------------------+--------------------+-----------------+--------------------+-----------+--------------------+-------------------+--------------------+-----------+-----------------+------------+-----------+
|org.apache.spark....|           1310|        display(df2)|org.apache.spark....|   == Physical Plan ...|{"nodeName":"C

##### 3.4.1 Create unique ids for each physical plan and store them in a table
* Create table for storage of unique physical plan keys (**physical_plan_keys**)
* Combine sparkContextID, clusterInstanceID and executionID to create a unique id for each physical plan
* Store these keys in the table

This id is later used on the single operations which gives us a way of seeing which operations belong to which physical plan.

In [0]:
%sql
CREATE TABLE IF NOT EXISTS physical_plan_keys (
  sparkContextID STRING,
  clusterInstanceID STRING,
  executionID INT,
  physicalPlanKey INT
);

In [0]:
# Add a new column to the dataframe that concatenates the 'sparkContextID', 'clusterInstanceID', and 'executionID' columns
# This column will be used to generate a hash key later
sql_df = sql_df.withColumn(
    "concatPhysicalPlanKey",
    F.concat("sparkContextID", "clusterInstanceID", "executionID"),
)

# Generate a hash key from the 'concatPhysicalPlanKey' column and add it as a new column to the dataframe
sql_df = sql_df.withColumn("physicalPlanKey", F.hash("concatPhysicalPlanKey")).drop(
    "concatPhysicalPlanKey"
)

sql_df = sql_df.dropDuplicates(['physicalPlanKey'])

# Query the existing physical plan keys in the 'physical_plan_keys' table
existing_keys = spark.sql("select physicalPlanKey from physical_plan_keys")

# Select the distinct values of 'sparkContextID', 'clusterInstanceID', 'executionID', and 'physicalPlanKey' columns
# from the dataframe
new_keys = sql_df.select(
    "sparkContextID", "clusterInstanceID", "executionID", "physicalPlanKey"
).distinct()

# Perform an anti-join on the 'physicalPlanKey' column between the new keys and the existing keys to keep only the keys
# that don't already exist in the 'physical_plan_keys' table
# This should not really be the case, but added as a failsafe if you are read the same physical plans multiple times
new_keys = new_keys.join(existing_keys, "physicalPlanKey", "anti")

# Write the new keys to the 'physical_plan_keys' table
print(f"Adding {new_keys.count()} new keys to the physicalPlanKey table")
new_keys.write.mode("append").saveAsTable("default.physical_plan_keys")

Adding 10210 new keys to the physicalPlanKey table


##### 3.5 Extract Information From Physical Plan  
###### Final Table  
- **execution_id** (same as Spark queryID)
- **operation** (type of operation, e.g. Filter, ..)
- **column_id** (unique global id of the column the operation is performed on)
- **timestamp**  
- **condition**  (e.g. greaterThan)
- **conditionValue** (e.g. 5)

In [0]:
physical_plan_df = sql_df.select(
    F.col("executionId"),
    F.col("time_start").alias("timestamp"),
    F.col("physicalPlanDescription"),
    F.col("physicalPlanKey"),
    "eventlogKey",
)

physical_plan_df.show(5)

+-----------+-----------------+-----------------------+---------------+-----------+
|executionId|        timestamp|physicalPlanDescription|physicalPlanKey|eventlogKey|
+-----------+-----------------+-----------------------+---------------+-----------+
|        976|1.682034474802E12|   == Physical Plan ...|    -2140848050|   85799799|
|          0| 1.68133340762E12|   == Physical Plan ...|    -2139115355| -371546082|
|         49|1.682505485759E12|   == Physical Plan ...|    -2137141090| -302499034|
|        302|1.682594864853E12|   == Physical Plan ...|    -2135497522| 1563319382|
|        385|1.682029605382E12|   == Physical Plan ...|    -2132409082|-1937385617|
+-----------+-----------------+-----------------------+---------------+-----------+
only showing top 5 rows



#### 3.5.0 Filter unrelevant physical plans
* Check for plans that include a FileScan opearator (i.e. Scan Parquet ...)
* May add more in the future as there could be different ways of storing data than parquet
* Also, not every query is reading from disk

In [0]:
physical_plan_filtered_df = physical_plan_df.filter(
    F.col("physicalPlanDescription").like("%Scan parquet%")
)

#### 3.5.1 Create Column Lookup Dictionary  
- A dictionary to bind columns to table and database

In [0]:
def create_column_lookup(physicalPlan):
    COLUMN_LOOKUP = {}

    # first part of this regex will capture the spark_catalog.database.column_name part of the filescan
    # second part of the regex will capture all the columns in the following line
    regex = r"\(\d+\)\s+Scan parquet\s+(\S+)\nOutput \[\d+\]: \[(.*?)\]"
    matches = re.findall(regex, physicalPlan)

    for m in matches:
        db_table = m[0]  # first capture group
        database, table = db_table.split(".")[-2:]

        columns = m[1]  # second capture group
        for c in columns.split(", "):
            COLUMN_LOOKUP[c] = {"database": database, "table": table}
    return COLUMN_LOOKUP


# User defined function to perform on dataframe
col_lookup_udf = F.udf(
    create_column_lookup,
    MapType(StringType(), MapType(StringType(), StringType()), False),
)

In [0]:
# Create column lookup column
physical_plan_lookup_df = physical_plan_filtered_df.withColumn(
    "columnLookup", col_lookup_udf("physicalPlanDescription")
)

## Example of a scan parquet where NO LOOKUP is built:

    (1) Scan parquet 
    Output [1]: [wdayEffect#24088]
    Batched: true
    Location: PreparedDeltaFileIndex [dbfs:/mnt/lake/process/raw/gassco/output/bookings_for_companies_with_rebooking/v1r0]
    ReadSchema: struct<wdayEffect:string>

In [0]:
# Filter out only sql queries which contains lookup dictionary
physical_plan_lookup_df = physical_plan_lookup_df.filter(F.size("columnLookup") > 0)

#### 3.5.2 Use Regex To Find Relevant Information
- `Filter`
- `DataFilter`  
- `PushedFilters`  
- `PartitionFilters`  

##### `NOTE` Still one problem have no idea how to make the operation_id the way we planed. As it is now it has same operation id for operations from same physical plan  
##### `NOTE` Also a lot of operation rows are missing database and table

In [0]:
def build_rows(
    columns,
    column_lookup,
    operation_name,
    execution_id,
    timestamp,
    physical_plan_key,
    eventlog_key,
    table=None,
    database=None,
):
    unique_columns = set(columns)
    rows = []
    for c in unique_columns:
        # If you are handling a pushed filter, the column lookup might not be available
        # this is when the table and database variables ARE provided
        if database is None:
            database = column_lookup.get(c, {}).get("database", "")
        if table is None:
            table = column_lookup.get(c, {}).get("table", "")

        rows.append(
            {
                "operationName": operation_name,
                "executionId": execution_id,
                "databaseName": database,
                "tableName": table,
                "columnName": c.split("#")[0],  # get the part before the #
                "timeGenerated": timestamp,
                "physicalPlanKey": physical_plan_key,
                "eventlogKey": eventlog_key,
            }
        )
    return rows

In [0]:
def plan_parser(row, name, regex, col_regex, group_index):
    """Performs parsing of physical plan in dataframe row

    Args:
        row[spark.row]: Row in dataframe
        name[string]: Name of operation
        regex[string]: Regex for parsing after operation
        col_regex[string]: Regex for parsing column (different for pushedFilters so needed as input)
        group_index[integer]: Index for group in regex to get data frin
    Returns:
        A list of dictionarys/rows for new dataframe
        row_lst: list[dict]

    """
    # Define inputs
    execution_id = row["executionId"]
    timestamp = row["timestamp"]
    physical_plan = row["physicalPlanDescription"]
    column_lookup = row["columnLookup"]
    physical_plan_key = row["physicalPlanKey"]
    eventlog_key = row["eventlogKey"]

    # List containing instances
    row_lst = []
    # Matches for provided regex and loop through each
    matches = re.findall(regex, physical_plan)
    for m in matches:
        # Find relevant condtion group
        cond_group = m[group_index]
        # Find columns in condition group
        columns = re.findall(col_regex, cond_group)

        if name == "PushedFilters":  # Missing internal id so needs a small tweak
            # Find for pushed group
            # first capture group in file scan is: somethinghere.database.table
            db_table = m[0]
            database, table = db_table.split(".")[-2:]

            rows = build_rows(
                columns,
                column_lookup,
                name,
                execution_id,
                timestamp,
                physical_plan_key,
                eventlog_key,
                table=table,
                database=database,
            )
        else:
            rows = build_rows(
                columns,
                column_lookup,
                name,
                execution_id,
                timestamp,
                physical_plan_key,
                eventlog_key,
            )
        row_lst.extend(rows)

    return row_lst


def multi_plan_parser(row, settings):

    row_instances = []

    for operation in settings:
        operation_rows = plan_parser(
            row,
            operation["operation_name"],
            operation["regex"],
            operation["col_regex"],
            operation["group_index"],
        )
        row_instances.extend(operation_rows)
    return row_instances

In [0]:
# unique id for each of the opeartions
latest_operation_id = 0

# update latest_operation_id if there exists opeartions from before
if spark.catalog.tableExists("operations"):
    prev_operation_id = spark.sql(
        "SELECT MAX(operationId) AS operationId FROM operations"
    )
    latest_operation_id = prev_operation_id.collect()[0]["operationId"]

print(f"Previouis Operation ID: {latest_operation_id}")

Previouis Operation ID: 777


In [0]:
settings = [
    {
        "operation_name": "Filter",
        "regex": "\(\d+\)\s+Filter(.*?\n)Input(.*?\n)Condition : (.*?)\n\n",
        "col_regex": "\w+#\d+",
        "group_index": -1,
    },
    {
        "operation_name": "PartitionFilters",
        "regex": "\(\d+\)\s+Scan parquet\s+(\S+)\nOutput \[\d+\]: \[(.*?)\]\n(.*?\n)Location:(.*?\n)?(PartitionFilters:\s\[(.*?)\]\n)",
        "col_regex": "\w+#\d+",
        "group_index": -1,
    },
    {
        "operation_name": "PushedFilters",
        "regex": "\(\d+\)\s+Scan parquet\s+(\S+)\nOutput \[\d+\]: \[(.*?)\]\n(.*?\n)Location:(.*?\n)?(PartitionFilters:\s\[(.*?)\]\n)?(PushedFilters:\s\[(.*?)\])?",
        "col_regex": r"(?<=\()\b(?:[^(),]+|\((?:[^(),]+|\((?:[^(),]+|\((?:[^(),]+|\([^()]*\))*\))*\))*)(?=,|\))",
        "group_index": -1,
    },
]


operation_rdd = physical_plan_lookup_df.rdd.map(
    lambda row: multi_plan_parser(row, settings)
)
operation_df = operation_rdd.flatMap(lambda l: l).toDF()
operation_df = operation_df.withColumn(
    "operationId", F.monotonically_increasing_id() + latest_operation_id
)

In [0]:
# Convert string to int so that it can be used for comparison at a later stage (rulebased notebook)

operation_df = operation_df.withColumn(
    "timeGenerated", F.col("timeGenerated").cast("bigint")
)

operation_df.printSchema()
operation_df.show()

root
 |-- columnName: string (nullable = true)
 |-- databaseName: string (nullable = true)
 |-- eventlogKey: long (nullable = true)
 |-- executionId: long (nullable = true)
 |-- operationName: string (nullable = true)
 |-- physicalPlanKey: long (nullable = true)
 |-- tableName: string (nullable = true)
 |-- timeGenerated: long (nullable = true)
 |-- operationId: long (nullable = false)

+--------------------+------------+-----------+-----------+-------------+---------------+------------+-------------+-----------+
|          columnName|databaseName|eventlogKey|executionId|operationName|physicalPlanKey|   tableName|timeGenerated|operationId|
+--------------------+------------+-----------+-----------+-------------+---------------+------------+-------------+-----------+
|           tableName|     default| 1049959353|        246|       Filter|    -2012069072|  operations|1682160382506|        777|
|        databaseName|     default| 1049959353|        246|       Filter|    -2012069072|  ope

### 4. Write to Delta Table

#####`NOTE` WE ARE SAVING FILES INTO A PATH ALREADY THAT IS NOT IN DELTA FORMAT; WE NEED TO CHOOSE NEW PATH FOR THE DELTA FORMAT OR DELETE EXISTING FILES THERE  
##### WE ALSO HAVE TO FIX DUPLICATE PROBLEM FOR BOTH NOTEBOOKS WHEN LOADING TO TABLE ... (MERGE) https://stackoverflow.com/questions/67920919/how-to-prevent-duplicate-entries-to-enter-to-delta-lake-of-azure-storage

##### 4.2 Spark Operations Table

In [0]:
operation_df.printSchema()

root
 |-- columnName: string (nullable = true)
 |-- databaseName: string (nullable = true)
 |-- eventlogKey: long (nullable = true)
 |-- executionId: long (nullable = true)
 |-- operationName: string (nullable = true)
 |-- physicalPlanKey: long (nullable = true)
 |-- tableName: string (nullable = true)
 |-- timeGenerated: long (nullable = true)
 |-- operationId: long (nullable = false)



In [0]:
%sql
CREATE TABLE IF NOT EXISTS operations (
  columnName STRING,
  databaseName STRING,
  executionId LONG,
  operationName STRING,
  physicalPlanKey LONG,
  eventlogKey LONG,
  tableName STRING,
  timeGenerated LONG,
  operationId LONG
)

In [0]:
# Load eventlogKeys from existing data
existing_keys = spark.sql("select eventlogKey from operations")

print(f"Size of new operations before filtering {operation_df.count()}")

# Perform anti-join on eventlogKeys to make sure the new data isnt a duplicate of what is already stored in the table
operation_df = operation_df.join(existing_keys, "eventlogKey", "anti")

print(f"Size of new operations after filtering {operation_df.count()}")

# Load data to delta table
delta_table_path = "dbfs:/mnt/lake/"
operation_df.write.format("delta").mode("append").saveAsTable("operations")

Size of new operations before filtering 7267
Size of new operations after filtering 7267


##### 4.3 Queries Table

Create a queries-table that can be joined with the operations table to get more information with each opeartion.

In [0]:
sql_df.printSchema()

root
 |-- event_start: string (nullable = true)
 |-- rootExecutionId: string (nullable = true)
 |-- Description: string (nullable = true)
 |-- Details: string (nullable = true)
 |-- physicalPlanDescription: string (nullable = true)
 |-- sparkPlanInfo: string (nullable = true)
 |-- time_start: double (nullable = true)
 |-- modifiedConfigs: string (nullable = true)
 |-- eventlogKey: integer (nullable = true)
 |-- event_end: string (nullable = true)
 |-- sparkContextID: string (nullable = true)
 |-- clusterInstanceID: string (nullable = true)
 |-- executionId: integer (nullable = true)
 |-- time_end: double (nullable = true)
 |-- errorMessage: string (nullable = true)
 |-- duration_ms: double (nullable = true)
 |-- physicalPlanKey: integer (nullable = false)



In [0]:
%sql
CREATE TABLE IF NOT EXISTS queries (
  event_start STRING,
  rootExecutionId STRING,
  Description STRING,
  Details STRING,
  physicalPlanDescription STRING,
  sparkPlanInfo STRING,
  time_start DOUBLE,
  modifiedConfigs STRING,
  eventlogKey INT,
  event_end STRING,
  sparkContextID STRING,
  clusterInstanceID STRING,
  executionId INT,
  time_end DOUBLE,
  errorMessage STRING,
  duration_ms DOUBLE,
  physicalPlanKey INT
);

In [0]:
existing_keys = spark.sql("select physicalPlanKey from queries")

print(f"Size queries in dataframe {sql_df.count()}")

# Perform anti-join on eventlogKeys to make sure the new data isnt a duplicate of what is already stored in the table
filtered_sql_df = sql_df.join(existing_keys, "physicalPlanKey", "anti")

print(f"Size of new queries after filtering {sql_df.count()}")

# Load data to delta table
delta_table_path = "dbfs:/mnt/lake/"
filtered_sql_df.write.format("delta").option("mergeSchema", "true").mode("append").saveAsTable(
    "queries"
)

Size queries in dataframe 10210
Size of new queries after filtering 10210


In [0]:
%sql
SELECT
  *
FROM
  operations

columnName databaseName executionId operationName physicalPlanKey eventlogKey tableName timeGenerated operationId lastModified default 568 Filter -2113573252 848484182 eventlog_raw 1681726704046 42949673737 clusterInstanceID default 568 Filter -2113573252 848484182 eventlog_raw 1681726704046 42949673738 sparkContextID default 568 Filter -2113573252 848484182 eventlog_raw 1681726704046 42949673739 eventData 568 Filter -2113573252 848484182 1681726704046 42949673740 clusterInstanceID default 568 Filter -2113573252 848484182 eventlog_raw 1681726704046 42949673741 sparkContextID default 568 Filter -2113573252 848484182 eventlog_raw 1681726704046 42949673742 lastModified default 568 Filter -2113573252 848484182 eventlog_raw 1681726704046 42949673743 eventData 568 Filter -2113573252 848484182 1681726704046 42949673744 sparkContextID default 568 PushedFilters -2113573252 848484182 eventlog_raw 1681726704046 42949673745 lastModified default 568 PushedFilters -2113573252 848484182 eventlog_raw 1681726704046 42949673746 clusterInstanceID default 568 PushedFilters -2113573252 848484182 eventlog_raw 1681726704046 42949673747 sparkContextID default 568 PushedFilters -2113573252 848484182 eventlog_raw 1681726704046 42949673748 lastModified default 568 PushedFilters -2113573252 848484182 eventlog_raw 1681726704046 42949673749 clusterInstanceID default 568 PushedFilters -2113573252 848484182 eventlog_raw 1681726704046 42949673750 lastModified default 131 Filter -2090983642 1135414734 eventlog_raw 1680782429230 42949673751 eventData 131 Filter -2090983642 1135414734 1680782429230 42949673752 lastModified default 131 Filter -2090983642 1135414734 eventlog_raw 1680782429230 42949673753 eventData 131 Filter -2090983642 1135414734 1680782429230 42949673754 lastModified default 131 Filter -2090983642 1135414734 eventlog_raw 1680782429230 42949673755 eventData 131 Filter -2090983642 1135414734 1680782429230 42949673756 lastModified default 131 Filter -2090983642 1135414734 eventlog_raw 1680782429230 42949673757 eventData 131 Filter -2090983642 1135414734 1680782429230 42949673758 lastModified default 131 PushedFilters -2090983642 1135414734 eventlog_raw 1680782429230 42949673759 lastModified default 131 PushedFilters -2090983642 1135414734 eventlog_raw 1680782429230 42949673760 lastModified default 111 Filter -2059523771 -1096060644 eventlog_raw 1681291013724 42949673761 eventData 111 Filter -2059523771 -1096060644 1681291013724 42949673762 lastModified default 111 PushedFilters -2059523771 -1096060644 eventlog_raw 1681291013724 42949673763 eventlogKey default 397 Filter -2012970020 1207902865 eventlog_raw 1681740276449 42949673764 eventlogKey default 397 PushedFilters -2012970020 1207902865 eventlog_raw 1681740276449 42949673765 lastModified default 127 Filter -2005737048 -178588093 eventlog_raw 1680599925386 42949673766 eventData 127 Filter -2005737048 -178588093 1680599925386 42949673767 lastModified default 127 Filter -2005737048 -178588093 eventlog_raw 1680599925386 42949673768 eventData 127 Filter -2005737048 -178588093 1680599925386 42949673769 lastModified default 127 PushedFilters -2005737048 -178588093 eventlog_raw 1680599925386 42949673770 lastModified default 127 PushedFilters -2005737048 -178588093 eventlog_raw 1680599925386 42949673771 eventData 238 Filter -1970545870 679725161 1681336365352 42949673772 clusterInstanceID default 238 Filter -1970545870 679725161 eventlog_raw 1681336365352 42949673773 lastModified default 238 Filter -1970545870 679725161 eventlog_raw 1681336365352 42949673774 sparkContextID default 238 Filter -1970545870 679725161 eventlog_raw 1681336365352 42949673775 eventData 238 Filter -1970545870 679725161 1681336365352 42949673776 sparkContextID default 238 PushedFilters -1970545870 679725161 eventlog_raw 1681336365352 42949673777 lastModified default 238 PushedFilters -1970545870 679725161 eventlog_raw 1681336365352 42949673778 clusterInstanceID default 238 PushedFilters -1970545870 679725161 eventlog_raw 16813363

In [0]:
%sql
SELECT
  *
FROM
  queries

event_start rootExecutionId Description Details physicalPlanDescription sparkPlanInfo time_start modifiedConfigs eventlogKey event_end sparkContextID clusterInstanceID executionId time_end errorMessage duration_ms physicalPlanKey org.apache.spark.sql.execution.ui.SparkListenerSQLExecutionStart 184 use catalog `hive_metastore`; describe database... org.apache.spark.sql.Dataset.collectResult(Dataset.scala:3416)
com.databricks.backend.daemon.driver.OutputAggregator$.withOutputAggregation0(OutputAggregator.scala:267)
com.databricks.backend.daemon.driver.OutputAggregator$.withOutputAggregation(OutputAggregator.scala:101)
com.databricks.backend.daemon.driver.SQLDriverLocal.executeSql(SQLDriverLocal.scala:115)
com.databricks.backend.daemon.driver.SQLDriverLocal.repl(SQLDriverLocal.scala:145)
com.databricks.backend.daemon.driver.DriverLocal.$anonfun$execute$23(DriverLocal.scala:729)
com.databricks.unity.EmptyHandle$.runWith(UCSHandle.scala:124)
com.databricks.backend.daemon.driver.DriverLocal.$anonfun$execute$20(DriverLocal.scala:712)
com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:398)
scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
com.databricks.logging.AttributionContext$.withValue(AttributionContext.scala:147)
com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:396)
com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:393)
com.databricks.backend.daemon.driver.DriverLocal.withAttributionContext(DriverLocal.scala:62)
com.databricks.logging.UsageLogging.withAttributionTags(UsageLogging.scala:441)
com.databricks.logging.UsageLogging.withAttributionTags$(UsageLogging.scala:426)
com.databricks.backend.daemon.driver.DriverLocal.withAttributionTags(DriverLocal.scala:62)
com.databricks.backend.daemon.driver.DriverLocal.execute(DriverLocal.scala:689)
com.databricks.backend.daemon.driver.DriverWrapper.$anonfun$tryExecutingCommand$1(DriverWrapper.scala:622)
scala.util.Try$.apply(Try.scala:213) == Physical Plan ==
CollectLimit (3)
+- CommandResult (1)
 +- DescribeNamespace (2)


(1) CommandResult
Output [2]: [database_description_item#1373, database_description_value#1374]
Arguments: [database_description_item#1373, database_description_value#1374]

(2) DescribeNamespace
Arguments: [database_description_item#1373, database_description_value#1374], com.databricks.sql.managedcatalog.UnityCatalogV2Proxy@5b8f3995, [default], true

(3) CollectLimit
Input [2]: [database_description_item#1373, database_description_value#1374]
Arguments: 10001

 {"nodeName":"CollectLimit","simpleString":"CollectLimit 10001","children":[{"nodeName":"CommandResult","simpleString":"CommandResult [database_description_item#1373, database_description_value#1374]","children":[],"metadata":{},"metrics":[{"name":"number of output rows","accumulatorId":2442,"metricType":"sum","experimental":false}],"explainId":null}],"metadata":{},"metrics":[{"name":"shuffle records written","accumulatorId":2440,"metricType":"sum","experimental":false},{"name":"records read","accumulatorId":2438,"metricType":"sum","experimental":false},{"name":"local bytes read","accumulatorId":2436,"metricType":"size","experimental":false},{"name":"fetch wait time","accumulatorId":2437,"metricType":"timing","experimental":false},{"name":"remote bytes read","accumulatorId":2434,"metricType":"size","experimental":false},{"name":"local blocks read","accumulatorId":2433,"metricType":"sum","experimental":false},{"name":"remote blocks read","accumulatorId":2432,"metricType":"sum","experimental":false},{"name":"remote bytes read to disk","accumulatorId":2435,"metricType":"size","experimental":false},{"name":"shuffle bytes written","accumulatorId":2439,"metricType":"size","experimental":false}],"explainId":null} 1.679485119956E12 {"spark.r.sql.derby.temp.dir":"/tmp/RtmpPe0TrA"} 2042027793 org.apache.spark.sql.execution.ui.SparkListenerSQLExecutionEnd 1779129196434913561 1220-124459-5lnjmtzx_10_254_10_44 184 1.

In [0]:
%sql
SELECT
  *
FROM
  physical_plan_keys

sparkContextID clusterInstanceID executionID physicalPlanKey 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 353 -2146934606 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 606 -2146784117 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 1287 -2146209763 7643291139468147288 1220-124459-5lnjmtzx_10_254_10_8 158 -2145286336 3952163646167870121 1220-124459-5lnjmtzx_10_254_10_22 516 -2145055373 7033256278058855708 1220-124459-5lnjmtzx_10_254_10_13 31 -2145019305 5831612348755309262 1220-124459-5lnjmtzx_10_254_10_5 16 -2144949261 2296910109933074401 1220-124459-5lnjmtzx_10_254_10_8 11 -2143362574 919268754167096745 1220-124459-5lnjmtzx_10_254_10_33 393 -2142958139 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 826 -2142320414 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 976 -2140848050 8800158164924010054 1220-124459-5lnjmtzx_10_254_10_6 0 -2139115355 5391835918080460643 1220-124459-5lnjmtzx_10_254_10_31 580 -2138275155 1363313670177219382 1220-124459-5lnjmtzx_10_254_10_38 220 -2137885004 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 139 -2137378661 2926626622541416826 1220-124459-5lnjmtzx_10_254_10_29 49 -2137141090 7557011926774407381 1220-124459-5lnjmtzx_10_254_10_21 571 -2136353319 2272446215719826247 1220-124459-5lnjmtzx_10_254_10_12 68 -2136214369 5391835918080460643 1220-124459-5lnjmtzx_10_254_10_31 614 -2136009088 6468036725450673267 1220-124459-5lnjmtzx_10_254_10_43 302 -2135497522 7557011926774407381 1220-124459-5lnjmtzx_10_254_10_21 726 -2135399923 2992981800875966013 1220-124459-5lnjmtzx_10_254_10_19 416 -2134102827 5391835918080460643 1220-124459-5lnjmtzx_10_254_10_31 447 -2133966371 7557011926774407381 1220-124459-5lnjmtzx_10_254_10_21 83 -2133819075 8800158164924010054 1220-124459-5lnjmtzx_10_254_10_6 144 -2133606790 3952163646167870121 1220-124459-5lnjmtzx_10_254_10_22 374 -2133374646 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 627 -2133265091 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 385 -2132409082 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 784 -2131600342 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 1071 -2130773814 919268754167096745 1220-124459-5lnjmtzx_10_254_10_33 565 -2129828703 7557011926774407381 1220-124459-5lnjmtzx_10_254_10_21 485 -2129317854 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 963 -2128779989 7195996001498078531 1220-124459-5lnjmtzx_10_254_10_27 13 -2128648625 7843435730741643678 1220-124459-5lnjmtzx_10_254_10_7 23 -2128220870 3952163646167870121 1220-124459-5lnjmtzx_10_254_10_22 241 -2127635058 2751788431714625779 1220-124459-5lnjmtzx_10_254_10_12 681 -2127575998 2296910109933074401 1220-124459-5lnjmtzx_10_254_10_8 91 -2127510143 2992981800875966013 1220-124459-5lnjmtzx_10_254_10_19 336 -2126975351 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 78 -2125837193 3952163646167870121 1220-124459-5lnjmtzx_10_254_10_22 356 -2125540769 1363313670177219382 1220-124459-5lnjmtzx_10_254_10_38 467 -2125362410 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 570 -2125324127 6468036725450673267 1220-124459-5lnjmtzx_10_254_10_43 10 -2124264777 919268754167096745 1220-124459-5lnjmtzx_10_254_10_33 679 -2124178303 1640061253313066459 1220-124459-5lnjmtzx_10_254_10_7 34 -2123984120 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 839 -2123761895 3286691063738442855 1220-124459-5lnjmtzx_10_254_10_24 29 -2123534537 919268754167096745 1220-124459-5lnjmtzx_10_254_10_33 238 -2123437766 2861951072945299053 1220-124459-5lnjmtzx_10_254_10_9 563 -2123414665 2992981800875966013 1220-124459-5lnjmtzx_10_254_10_19 238 -2121716175 7557011926774407381 1220-124459-5lnjmtzx_10_254_10_21 331 -2120889846 8800158164924010054 1220-124459-5lnjmtzx_10_254_10_6 45 -2120542496 2296910109933074401 1220-124459-5lnjmtzx_10_254_10_8 134 -2120363845 7195996001498078531 1220-124459-5lnjmtzx_10_254_10_27 14 -2119900592 2272446215719826247 1220-124459-5lnjmtzx_10_254_10_12 153 -2119833085 2992981800875966013 1220-124459-5lnjmtzx_10_254_10_19 10